In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import networkx as nx
from sklearn.neighbors import NearestNeighbors
from copy import deepcopy
import pylcs as lcs
import utils as ut

In [2]:
cells = pd.read_csv('data/cells_no_repeats.csv', index_col=0)
cells.set_index('pt_root_id', inplace=True)
print(cells.shape)
display(cells.head())

synapses_all = pd.read_csv('data/synapses_w_ids.csv', index_col=0)
synapses_all.set_index('synapse_id', inplace=True)
print(synapses_all.shape)
display(synapses_all.head())

(56209, 4)


cell_type   pt_x    pt_y   pt_z
pt_root_id                                        
864691135639004475       23P  71136  110528  20220
864691135771677771       23P  72576  108656  20291
864691135864089470       23P  79632  121456  16754
864691135560505569       23P  80128  124000  16563
864691136315868311       23P  80144  126928  16622

(5421809, 17)


pre_pt_root_id     post_pt_root_id   size cell_type_pre  \
synapse_id                                                                
0           864691135564683351  864691136811959667    960           23P   
1           864691135614119115  864691135508912649   7576           23P   
3           864691135113147801  864691136022555784    684           23P   
4           864691135194393642  864691135341362885  23172           23P   
5           864691136272938174  864691135683554546   3660           23P   

            cb_x_pre  cb_y_pre  cb_z_pre cell_type_post  cb_x_post  cb_y_post  \
synapse_id                                                                      
0            557.248   570.560    732.52            23P    791.744    483.968   
1            774.720   504.960    895.68            23P    807.936    459.584   
3            883.072   451.456    817.84            23P    851.520    483.840   
4            781.248   449.984    696.88            23P    798.720    465.152   
5            762.368   473.792    773.68            23P    820.352    446.784   

            cb_z_post  cb_x_diff  cb_y_diff  cb_z_diff  ctr_pt_x  ctr_pt_y  \
synapse_id                                                                   
0              780.44   -234.496     86.592     -47.92   637.608   371.352   
1              870.28    -33.216     45.376      25.40   805.376   488.376   
3              759.96     31.552    -32.384      57.88   858.328   516.648   
4              758.56    -17.472    -15.168     -61.68   789.400   478.040   
5              719.08    -57.984     27.008      54.60   756.624   440.928   

            ctr_pt_z  
synapse_id            
0             720.20  
1             863.60  
3             775.88  
4             691.00  
5             710.60

In [3]:
key_columns = ['pre_pt_root_id', 'post_pt_root_id', 'cell_type_pre', 'ctr_pt_x', 'ctr_pt_y', 'ctr_pt_z']
synapses = synapses_all.loc[:, key_columns]
display(synapses.head())

pre_pt_root_id     post_pt_root_id cell_type_pre  ctr_pt_x  \
synapse_id                                                                   
0           864691135564683351  864691136811959667           23P   637.608   
1           864691135614119115  864691135508912649           23P   805.376   
3           864691135113147801  864691136022555784           23P   858.328   
4           864691135194393642  864691135341362885           23P   789.400   
5           864691136272938174  864691135683554546           23P   756.624   

            ctr_pt_y  ctr_pt_z  
synapse_id                      
0            371.352    720.20  
1            488.376    863.60  
3            516.648    775.88  
4            478.040    691.00  
5            440.928    710.60

In [4]:
msts, _ = ut.generate_msts(synapses, cells, k=6, soma_k=15)

864691134884741370, 1/56179, 1.7800245643389878e-05: 87 nodes, 86 edges
864691134884741626, 2/56179, 3.5600491286779756e-05: 74 nodes, 73 edges
864691134884742138, 3/56179, 5.3400736930169635e-05: 52 nodes, 51 edges
864691134884742906, 4/56179, 7.120098257355951e-05: 164 nodes, 163 edges
864691134884743162, 5/56179, 8.900122821694939e-05: 48 nodes, 47 edges
864691134884743418, 6/56179, 0.00010680147386033927: 100 nodes, 99 edges
864691134884743930, 7/56179, 0.00012460171950372915: 139 nodes, 138 edges
864691134884745210, 8/56179, 0.00014240196514711903: 122 nodes, 121 edges
864691134884747002, 9/56179, 0.0001602022107905089: 234 nodes, 233 edges
864691134884747514, 10/56179, 0.00017800245643389878: 36 nodes, 35 edges
864691134884748026, 11/56179, 0.00019580270207728866: 185 nodes, 184 edges
864691134884748282, 12/56179, 0.00021360294772067854: 106 nodes, 105 edges
864691134884749562, 13/56179, 0.00023140319336406842: 91 nodes, 90 edges
864691134884749818, 14/56179, 0.000249203439007458

In [10]:
# For each minimum spanning tree, extract its paths and save them to a pandas dataframe, preserving the cell id of the mst
# Since the paths have differing lengths, we will pad them with -1 to make them all the same length
def extract_sequences(msts):
    sequences = []
    for i, mst in enumerate(msts):
        cell_id = mst.graph['cell_id']
        paths = ut.get_paths(mst, -1)
        for path in paths:
            if len(path) > 2:
                sequences.append([cell_id] + path)
        print(f'{i / len(msts)}: Extracted {len(paths)} sequences from cell {cell_id}')
    sequences = pd.DataFrame(sequences)
    sequences.fillna(-1, inplace=True)

    # Name the columns of sequences
    sequences.columns = ['cell_id'] + [f'synapse_rank_{i}' for i in range(sequences.shape[1] - 1)]
    return sequences

In [11]:
sequences = extract_sequences(msts)

0.0: Extracted 39 sequences from cell 864691134884741370
1.797365062817909e-05: Extracted 39 sequences from cell 864691134884741626
3.594730125635818e-05: Extracted 22 sequences from cell 864691134884742138
5.392095188453727e-05: Extracted 55 sequences from cell 864691134884742906
7.189460251271635e-05: Extracted 26 sequences from cell 864691134884743162
8.986825314089545e-05: Extracted 32 sequences from cell 864691134884743418
0.00010784190376907454: Extracted 39 sequences from cell 864691134884743930
0.00012581555439725362: Extracted 52 sequences from cell 864691134884745210
0.0001437892050254327: Extracted 72 sequences from cell 864691134884747002
0.0001617628556536118: Extracted 12 sequences from cell 864691134884747514
0.0001797365062817909: Extracted 60 sequences from cell 864691134884748026
0.00019771015690997: Extracted 34 sequences from cell 864691134884748282
0.00021568380753814908: Extracted 29 sequences from cell 864691134884749562
0.00023365745816632816: Extracted 52 seque

In [13]:
display(sequences.head())

cell_id  synapse_rank_0  synapse_rank_1  synapse_rank_2  \
0  864691134884741370          932857          979837          958004   
1  864691134884741370          968986          965894          920902   
2  864691134884741370          915249          915025          977587   
3  864691134884741370          946081          934430          975852   
4  864691134884741370          897151          911679          940994   

   synapse_rank_3  synapse_rank_4  synapse_rank_5  synapse_rank_6  \
0        943204.0        899013.0            -1.0            -1.0   
1            -1.0            -1.0            -1.0            -1.0   
2            -1.0            -1.0            -1.0            -1.0   
3            -1.0            -1.0            -1.0            -1.0   
4        977661.0            -1.0            -1.0            -1.0   

   synapse_rank_7  synapse_rank_8  ...  synapse_rank_32  synapse_rank_33  \
0            -1.0            -1.0  ...             -1.0             -1.0   
1            -1.0            -1.0  ...             -1.0             -1.0   
2            -1.0            -1.0  ...             -1.0             -1.0   
3            -1.0            -1.0  ...             -1.0             -1.0   
4            -1.0            -1.0  ...             -1.0             -1.0   

   synapse_rank_34  synapse_rank_35  synapse_rank_36  synapse_rank_37  \
0             -1.0             -1.0             -1.0             -1.0   
1             -1.0             -1.0             -1.0             -1.0   
2             -1.0             -1.0             -1.0             -1.0   
3             -1.0             -1.0             -1.0             -1.0   
4             -1.0             -1.0             -1.0             -1.0   

   synapse_rank_38  synapse_rank_39  synapse_rank_40  synapse_rank_41  
0             -1.0             -1.0             -1.0             -1.0  
1             -1.0             -1.0             -1.0             -1.0  
2             -1.0             -1.0             -1.0             -1.0  
3             -1.0             -1.0             -1.0             -1.0  
4             -1.0             -1.0             -1.0             -1.0  

[5 rows x 43 columns]

In [19]:
# Convert the each sequence of synapse ids to a sequence of pre-synaptic cell ids
def synapse_to_cell(sequences, synapses):
    sequences_c = sequences.copy()
    sequences_c = sequences_c.astype(int)
    sequences_c = sequences_c.loc[:, sequences.columns != 'cell_id']

    map_func = lambda syn_id: synapses.loc[syn_id, 'pre_pt_root_id'] if syn_id != -1 else -1
    sequences_c = sequences_c.applymap(map_func)

    sequences_c.insert(0, 'cell_id', sequences['cell_id'])
    return sequences_c

In [20]:
true_sequences = synapse_to_cell(sequences, synapses_all)
display(true_sequences.head())

cell_id      synapse_rank_0      synapse_rank_1  \
0  864691134884741370  864691136388590711  864691136388590711   
1  864691134884741370  864691137197307201  864691135430634738   
2  864691134884741370  864691134884741370  864691135386779265   
3  864691134884741370  864691135915170150  864691135058541467   
4  864691134884741370  864691136952179935  864691135564534807   

       synapse_rank_2      synapse_rank_3      synapse_rank_4  synapse_rank_5  \
0  864691136388590711  864691136854122350  864691135428740656              -1   
1  864691135511060676                  -1                  -1              -1   
2  864691134884741370                  -1                  -1              -1   
3  864691135182111490                  -1                  -1              -1   
4  864691136020217336  864691135162572077                  -1              -1   

   synapse_rank_6  synapse_rank_7  synapse_rank_8  ...  synapse_rank_32  \
0              -1              -1              -1  ...               -1   
1              -1              -1              -1  ...               -1   
2              -1              -1              -1  ...               -1   
3              -1              -1              -1  ...               -1   
4              -1              -1              -1  ...               -1   

   synapse_rank_33  synapse_rank_34  synapse_rank_35  synapse_rank_36  \
0               -1               -1               -1               -1   
1               -1               -1               -1               -1   
2               -1               -1               -1               -1   
3               -1               -1               -1               -1   
4               -1               -1               -1               -1   

   synapse_rank_37  synapse_rank_38  synapse_rank_39  synapse_rank_40  \
0               -1               -1               -1               -1   
1               -1               -1               -1               -1   
2               -1               -1               -1               -1   
3               -1               -1               -1               -1   
4               -1               -1               -1               -1   

   synapse_rank_41  
0               -1  
1               -1  
2               -1  
3               -1  
4               -1  

[5 rows x 43 columns]

In [27]:
column_map = {f'synapse_rank_{i}': f'pre_id_rank_{i}' for i in range(sequences.shape[1] - 1)}
true_sequences.rename(columns=column_map, inplace=True)
display(true_sequences.head())
# true_sequences.to_csv('data/dendritic_sequences/dendritic_sequences.csv')

cell_id       pre_id_rank_0       pre_id_rank_1  \
0  864691134884741370  864691136388590711  864691136388590711   
1  864691134884741370  864691137197307201  864691135430634738   
2  864691134884741370  864691134884741370  864691135386779265   
3  864691134884741370  864691135915170150  864691135058541467   
4  864691134884741370  864691136952179935  864691135564534807   

        pre_id_rank_2       pre_id_rank_3       pre_id_rank_4  pre_id_rank_5  \
0  864691136388590711  864691136854122350  864691135428740656             -1   
1  864691135511060676                  -1                  -1             -1   
2  864691134884741370                  -1                  -1             -1   
3  864691135182111490                  -1                  -1             -1   
4  864691136020217336  864691135162572077                  -1             -1   

   pre_id_rank_6  pre_id_rank_7  pre_id_rank_8  ...  pre_id_rank_32  \
0             -1             -1             -1  ...              -1   
1             -1             -1             -1  ...              -1   
2             -1             -1             -1  ...              -1   
3             -1             -1             -1  ...              -1   
4             -1             -1             -1  ...              -1   

   pre_id_rank_33  pre_id_rank_34  pre_id_rank_35  pre_id_rank_36  \
0              -1              -1              -1              -1   
1              -1              -1              -1              -1   
2              -1              -1              -1              -1   
3              -1              -1              -1              -1   
4              -1              -1              -1              -1   

   pre_id_rank_37  pre_id_rank_38  pre_id_rank_39  pre_id_rank_40  \
0              -1              -1              -1              -1   
1              -1              -1              -1              -1   
2              -1              -1              -1              -1   
3              -1              -1              -1              -1   
4              -1              -1              -1              -1   

   pre_id_rank_41  
0              -1  
1              -1  
2              -1  
3              -1  
4              -1  

[5 rows x 43 columns]

In [33]:
# Convert each sequence of pre-synaptic cell ids to a single string of characters, where each character represents a unique cell id
def cell_to_char(sequences, id_to_char_map):
    sequences_c = sequences.copy()
    sequences_c = sequences_c.astype(int)
    sequences_c = sequences_c.loc[:, sequences.columns != 'cell_id']

    map_func = lambda cell_id: id_to_char_map[cell_id]
    sequences_c = sequences_c.applymap(map_func)

    sequences_c.insert(0, 'cell_id', sequences['cell_id'])
    return sequences_c

In [37]:
import math
import string

def map_to_printable_string(number, length):
    if 0 <= number <= 56208:
        printable_chars = string.printable[:-6]  # Exclude non-printable characters
        base = len(printable_chars)
        
        encoded = ""
        while number > 0:
            number, index = divmod(number, base)
            encoded = printable_chars[index] + encoded
        
        # Pad with leading zeros if needed
        padding = length - len(encoded)
        encoded = printable_chars[0] * padding + encoded
        
        return encoded
    else:
        raise ValueError("Number must be in the range 0 to 56208")

In [39]:
cell_ids = np.unique(true_sequences.values[:, 1:])

# Calculate the minimum string length needed
max_value = len(cell_ids) - 1
num_unique_chars = len(string.printable[:-6])  # Excluding non-printable characters
min_string_length = math.ceil(math.log(max_value + 1, num_unique_chars))

# # Example usage
# numbers = list(range(56209))  # List of numbers from 0 to 56208

# mapped_strings = [map_to_printable_string(number, min_string_length) for number in numbers]

# for number, mapped_string in zip(numbers, mapped_strings):
#     print(f"Number: {number} maps to Printable String: {mapped_string}")

In [40]:
# Map from cell_id to a single character, not safe to print, and back again
id_to_char_map = {cell_id: chr(i) for i, cell_id in enumerate(cell_ids)}
char_to_id_map = {v: k for k, v in id_to_char_map.items()}
id_to_char_map[-1] = ' '

# Map from cell_id to a printable string, safe to print, and back again
id_to_printable_string_map = {cell_id: '<' + map_to_printable_string(i, min_string_length) + '>' for i, cell_id in enumerate(cell_ids)}
printable_string_to_id_map = {v: k for k, v in id_to_printable_string_map.items()}

In [44]:
# Convert the sequences from lists of cell ids to single strings of characters
char_sequences = cell_to_char(true_sequences, id_to_char_map)

555981992164
